![](images/EscUpmPolit_p.gif "UPM")

# Course Notes for Learning Intelligent Systems

Department of Telematic Engineering Systems, Universidad Politécnica de Madrid, © Carlos A. Iglesias

# Table of Contents
* [Objectives](#Objectives)
* [Transformers](#Transformers)
* [Use cases: how to use pipelines](#Use-cases:-how-to-usepipelines)
    * Sentiment Analysis
    * Translation
    * Masked Word Completion
    * Text generation
    * Question Answering
    * Text to Speech
* [References](#References)

# Objectives

In this session we are going to learn the power of transformers.

# Transformers
As we saw, transformers are an extremely powerful architecture capable of performing many popular NLP tasks.

A well-known transformer model repository is available at https://huggingface.co/. 

Let's see how to use it. To go deeper, consult the Hugging tutorial (https://huggingface.co/learn/nlp-course/chapter1/1).

The transformers package requires to have installed Pytorch or TensorFlow. Check the installation details if you want to configure your environment well. For learning purposes, we are going to install Pytorch.


First of all, you should install Hugging Face. Execute:
* pip install torch transformers

In [1]:
!pip install torch transformers

In [2]:
!pip install huggingface_hub[hf_xet]

## Use cases: how to use pipelines

### Sentiment Analysis
Let's classify sentiments

In [3]:
from transformers import pipeline

from transformers import logging

logging.set_verbosity_error()
#logging.set_verbosity_warning()

model_sentiment = "cardiffnlp/twitter-roberta-base-sentiment-latest"

sentiment_pipe = pipeline("sentiment-analysis", model=model_sentiment)

print(sentiment_pipe("I love LLMs."))

#We pan 
print(sentiment_pipe(["I hate LLMs.", "I don't care about LLMs"]))

[{'label': 'positive', 'score': 0.974217414855957}]
[{'label': 'negative', 'score': 0.9310991168022156}, {'label': 'neutral', 'score': 0.5152539610862732}]


### Translation
Let's translate a sentence

In [4]:
from transformers import pipeline

#if no model is specified, it uses google-t5
translator_en_fr = pipeline("translation_en_to_fr")

print(translator_en_fr("This is the course of Natural Language Processing", max_length=40))

[{'translation_text': 'Il s’agit du cours de traitement des langues naturelles'}]


### Masked word completion
Generate words for a mask

In [6]:
from transformers import pipeline
unmasker = pipeline('fill-mask', model='bert-base-uncased')
unmasker("Hello, Im am eating at a [MASK].")

[{'score': 0.324342280626297,
  'token': 2795,
  'token_str': 'table',
  'sequence': 'hello, im am eating at a table.'},
 {'score': 0.3150157630443573,
  'token': 4825,
  'token_str': 'restaurant',
  'sequence': 'hello, im am eating at a restaurant.'},
 {'score': 0.07178673893213272,
  'token': 3347,
  'token_str': 'bar',
  'sequence': 'hello, im am eating at a bar.'},
 {'score': 0.042759791016578674,
  'token': 15736,
  'token_str': 'diner',
  'sequence': 'hello, im am eating at a diner.'},
 {'score': 0.032276567071676254,
  'token': 28305,
  'token_str': 'buffet',
  'sequence': 'hello, im am eating at a buffet.'}]

## Ner
Let's detect NER

In [7]:
from transformers import pipeline

ner = pipeline("ner", aggregation_strategy="simple")
ner("Peter has studied at Universidad Politécnica de Madrid in Madrid, Spain")

[{'entity_group': 'PER',
  'score': np.float32(0.9992756),
  'word': 'Peter',
  'start': 0,
  'end': 5},
 {'entity_group': 'ORG',
  'score': np.float32(0.98043567),
  'word': 'Universidad Politécnica de Madrid',
  'start': 21,
  'end': 54},
 {'entity_group': 'LOC',
  'score': np.float32(0.9985493),
  'word': 'Madrid',
  'start': 58,
  'end': 64},
 {'entity_group': 'LOC',
  'score': np.float32(0.99971014),
  'word': 'Spain',
  'start': 66,
  'end': 71}]

### Summarization
Let's generate a summary.

In [8]:
from transformers import pipeline

summarizer = pipeline("summarization", model="facebook/bart-large-cnn")

article = """
Europe’s climate chief has warned against politicians trying to use the climate crisis as a wedge issue in the forthcoming EU parliament elections, calling instead for climate policy that will bring wider economic benefits.
Wopke Hoekstra, the EU commissioner for climate action, said Europe had no choice but to press ahead with strong measures to cut greenhouse gases, whoever was in power, but added that more attention was needed to help businesses thrive in a low-carbon world.
He said: “There is no alternative than to continue with climate action. We need to continue in the direction of travel we have set. We need to speed up our pace.”
Rightwing parties are forecast in polls to do well in the election, to be held from 6 to 9 June, largely at the expense of the Greens and socialist parties. Protests by farmers in EU capitals have attacked climate policies, and some rightwing parties have stepped up anti-green rhetoric.
"""
print(summarizer(article, max_length=130, min_length=30, do_sample=False))                  

[{'summary_text': 'Wopke Hoekstra, the EU commissioner for climate action, said Europe had no choice but to press ahead with strong measures to cut greenhouse gases. He said more attention was needed to help businesses thrive in a low-carbon world.'}]


### Zero-shot classification
Classification without examples!

In [9]:
from transformers import pipeline
classifier = pipeline('zero-shot-classification', model='roberta-large-mnli')

sequence_to_classify = "one day I will see the world"
candidate_labels = ['travel', 'cooking', 'dancing']
classifier(sequence_to_classify, candidate_labels)

{'sequence': 'one day I will see the world',
 'labels': ['travel', 'cooking', 'dancing'],
 'scores': [0.9799639582633972, 0.010604996234178543, 0.009431015700101852]}

In [10]:
sequence_to_classify = "The CEO had a strong handshake."
candidate_labels = ['male', 'female']
hypothesis_template = "This text speaks about a {} profession."
classifier(sequence_to_classify, candidate_labels, hypothesis_template=hypothesis_template)

{'sequence': 'The CEO had a strong handshake.',
 'labels': ['male', 'female'],
 'scores': [0.8384836912155151, 0.16151626408100128]}

In [11]:
sentences = ["Nadal has won the last match", "There is an election in Bulgaria", "The oil price is very high", "The new film by Almodovar has been just released"]
candidate_labels = ['sport', 'politics', 'culture', 'economics']
classifier(sentences, candidate_labels)

[{'sequence': 'Nadal has won the last match',
  'labels': ['sport', 'culture', 'economics', 'politics'],
  'scores': [0.8608437180519104,
   0.07932601124048233,
   0.03197354078292847,
   0.027856681495904922]},
 {'sequence': 'There is an election in Bulgaria',
  'labels': ['politics', 'culture', 'economics', 'sport'],
  'scores': [0.962326169013977,
   0.015147211961448193,
   0.012851407751441002,
   0.009675218723714352]},
 {'sequence': 'The oil price is very high',
  'labels': ['economics', 'culture', 'politics', 'sport'],
  'scores': [0.846241295337677,
   0.06119693070650101,
   0.046528540551662445,
   0.04603324830532074]},
 {'sequence': 'The new film by Almodovar has been just released',
  'labels': ['culture', 'politics', 'sport', 'economics'],
  'scores': [0.7116525769233704,
   0.12886522710323334,
   0.10017038881778717,
   0.05931178107857704]}]

### Text generation
Let's generate

In [12]:
from transformers import pipeline

generation = pipeline("text-generation")

generation("This articles aims evaluating transformers' capabilities")


[{'generated_text': "This articles aims evaluating transformers' capabilities, its performance or its usefulness when applied to specific cases in which these transformers can be useful.\n\nA typical transformers in Java are given in the article Transformers. Since Java has many different classes"}]

### Question-Answering
Let's create a QA!

In [13]:
from transformers import pipeline

qa = pipeline("question-answering")

qa(
    question = "Where was born Penelope Cruz?",
    context = '''
               Cruz was born on April 28, 1974, in Alcobendas, Madrid, Spain. 
               In July 2010, Cruz married her Vicky Cristina Barcelona co-star, 
               Spanish actor Javier Bardem. The couple had begun dating early into filming, in 2007.
               '''
)

{'score': 0.8235689401626587,
 'start': 52,
 'end': 77,
 'answer': 'Alcobendas, Madrid, Spain'}

In [14]:
qa(
    question = "Who is Penelope Cruz' husband?",
    context = '''
               Cruz was born on April 28, 1974, in Alcobendas, Madrid, Spain. 
               In July 2010, Cruz married her Vicky Cristina Barcelona co-star,
               Spanish actor Javier Bardem. The couple had begun dating early into filming, in 2007.
               '''
)

{'score': 0.4068848490715027,
 'start': 126,
 'end': 202,
 'answer': 'Vicky Cristina Barcelona co-star,\n               Spanish actor Javier Bardem'}

### Text-to-Speech

In [15]:
from transformers import pipeline

pipe = pipeline("text-to-speech", model="suno/bark-small")
text = "[clears throat] This is a test ... and I just took a long pause."
output = pipe(text)

from IPython.display import Audio 

Audio(output["audio"], rate=output["sampling_rate"])

## References



* [Hugging Face Tutorial](https://huggingface.co/learn/nlp-course/chapter1/1) 

## Licence

The notebook is freely licensed under under the [Creative Commons Attribution Share-Alike license](https://creativecommons.org/licenses/by/2.0/).  

© Carlos A. Iglesias, Universidad Politécnica de Madrid.